In [2]:
import pandas as pd

df = pd.read_csv('analyzed.csv')
df = df.drop(['text', 'lemmatized', 'lemmatized_clean'], axis=1)
df.groupby('label').mean().head()

word_freq_mean  word_freq_75  word_freq_25   cefr_A1   cefr_A2   
label                                                                   
A1           0.000170      0.000185      0.000021  0.542096  0.415418  \
A2           0.000189      0.000202      0.000022  0.460254  0.400373   
B1           0.000219      0.000242      0.000022  0.348810  0.341909   
B2           0.000209      0.000236      0.000019  0.277349  0.289730   
C1           0.000180      0.000192      0.000014  0.230063  0.253246   

        cefr_B1   cefr_B2   cefr_C1   cefr_C2  
label                                          
A1     0.403081  0.317104  0.122436  0.141289  
A2     0.412394  0.331032  0.124915  0.147365  
B1     0.384167  0.322436  0.136989  0.149420  
B2     0.360757  0.322322  0.140191  0.155456  
C1     0.354457  0.336523  0.146551  0.157647

In [7]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, accuracy_score
import random
import numpy as np
# Random Seed at file level
random_seed = 54
np.random.seed(random_seed)
random.seed(random_seed)

X = df.drop('label', axis=1)
y = df['label']

# Encode labels
label_encoder = LabelEncoder()
y = label_encoder.fit_transform(y)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=True)

# Initialize and train the XGBoost classifier
#classifier = XGBClassifier(use_label_encoder=False, eval_metric='mlogloss')
classifier = RandomForestClassifier()
classifier.fit(X_train, y_train)

# Make predictions
y_pred = classifier.predict(X_test)

# Evaluate the model
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred, target_names=label_encoder.classes_)

print(f'Accuracy: {accuracy:.2f}')
print('Classification Report:')
print(report)

Accuracy: 0.52
Classification Report:
              precision    recall  f1-score   support

          A1       0.70      0.72      0.71        67
          A2       0.46      0.52      0.49        52
          B1       0.33      0.28      0.30        36
          B2       0.47      0.48      0.48        54
          C1       0.43      0.45      0.44        51
          C2       0.66      0.54      0.59        39

    accuracy                           0.52       299
   macro avg       0.51      0.50      0.50       299
weighted avg       0.52      0.52      0.52       299



In [8]:
import numpy as np

# Custom evaluation metrics
def custom_metrics(y_true, y_pred):
    y_true = np.array(y_true)
    y_pred = np.array(y_pred)
    correct = np.abs(y_true - y_pred) <= 1
    
    tp = np.sum(correct)
    fp = np.sum(~correct)
    fn = fp  # Since every incorrect prediction is a false positive and a false negative in this context

    precision = tp / (tp + fp) if (tp + fp) > 0 else 0
    recall = tp / (tp + fn) if (tp + fn) > 0 else 0
    f1 = 2 * precision * recall / (precision + recall) if (precision + recall) > 0 else 0
    
    accuracy = tp / len(y_true)
    
    return accuracy, precision, recall, f1

metrics = custom_metrics(y_test, y_pred)
print(metrics)

(0.9230769230769231, 0.9230769230769231, 0.9230769230769231, 0.9230769230769231)


In [9]:
import joblib
# Save the model to a file
joblib.dump(classifier, 'cefr_classifier.joblib')
joblib.dump(label_encoder, 'cefr_label_encoder.joblib')

['cefr_label_encoder.joblib']

In [10]:
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix

# Generate the confusion matrix
cm = confusion_matrix(y_test, y_pred)

# Plot the confusion matrix
plt.figure(figsize=(10, 7))
sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', xticklabels=label_encoder.classes_, yticklabels=label_encoder.classes_)
plt.xlabel('Predicted')
plt.ylabel('Actual')
plt.title('Confusion Matrix')
plt.show()


In [12]:
import time
from sklearn.inspection import permutation_importance
import pandas as pd

feature_names = ['word_freq_mean','word_freq_75','word_freq_25','cefr_A1','cefr_A2','cefr_B1','cefr_B2','cefr_C1','cefr_C2']
start_time = time.time()
result = permutation_importance(
    classifier, X_test, y_test, n_repeats=10, random_state=42, n_jobs=2
)
elapsed_time = time.time() - start_time
print(f"Elapsed time to compute the importances: {elapsed_time:.3f} seconds")

forest_importances = pd.Series(result.importances_mean, index=feature_names)
fig, ax = plt.subplots()
forest_importances.plot.bar(yerr=result.importances_std, ax=ax)
ax.set_title("Feature importances using permutation on full model")
ax.set_ylabel("Mean accuracy decrease")
fig.tight_layout()
plt.show()

Elapsed time to compute the importances: 0.567 seconds


In [35]:
from sklearn.tree import plot_tree

# Plot a single tree from the random forest
plt.figure(figsize=(300, 100))
plot_tree(classifier.estimators_[0], feature_names=feature_names, class_names=label_encoder.classes_, filled=True)
plt.title("Decision Tree from Random Forest")
plt.savefig('tree.png')